### Same as 2006WongWang but with deterministic integrator.

In [1]:
import os
import time
import subprocess

import numpy as np
import scipy.signal
import pandas as pd
import scipy.stats

from tvb.simulator.lab import *
from mne import time_frequency, filter
import plotly.graph_objects as go  # for data visualisation
import plotly.io as pio
from toolbox import timeseriesPlot, FFTplot, FFTpeaks, AEC, PLV, PLI, epochingTool, paramSpace

In [2]:
# This simulation will generate FC for a virtual "Subject".
# Define identifier (i.e. could be 0,1,11,12,...)
subjectid = ".2006WongWang"
wd=os.getcwd()
main_folder=wd+"\\"+subjectid
ctb_folder=wd+"\\CTB_data\\output\\"
if subjectid not in os.listdir(ctb_folder):
    os.mkdir(ctb_folder+subjectid)
    os.mkdir(main_folder)

emp_subj = "subj04"

# Prepare bimodality test (i.e. Hartigans' dip test in an external R script via python subprocess
# Build subprocess command: [Rscript, script]
# cmd = ['C:\\Program Files\\R\\R-3.6.1\\bin\\Rscript.exe',
#        'C:\\Users\\F_r_e\\PycharmProjects\\brainModels\\diptest\\diptest.R']

simLength = 1000 # ms - relatively long simulation to be able to check for power distribution
samplingFreq = 1000 #Hz
transient=200 # ms to exclude from timeseries due to initial transient

# integrator: dt=T(ms)=1000/samplingFreq(kHz)=1/samplingFreq(HZ)
# integrator = integrators.HeunStochastic(dt=1000/samplingFreq, noise=noise.Additive(nsig=np.array([0.01])))
integrator = integrators.HeunDeterministic(dt=1000/samplingFreq)

conn = connectivity.Connectivity.from_file(ctb_folder+"CTB_connx66_"+emp_subj+".zip")
conn.weights = conn.scaled_weights(mode="tract")

coup = coupling.Linear() # Wong-Wang Inh-Exc includes its own G coupling factor. 

mon = (monitors.Raw(),)

WARNING  File 'average_orientations' not found in ZIP.
WARNING  File 'cortical' not found in ZIP.
WARNING  File 'hemispheres' not found in ZIP.
WARNING  File 'areas' not found in ZIP.


# Wong-Wang Exc-Inh
-------

## Parameters from Deco (2014) - EE version

In [3]:
m = models.ReducedWongWangExcInh(G=np.array([1.3]), I_o=np.array([0.382]),
                                 J_N=np.array([0.15]), J_i=np.array([1]),
                                 W_e=np.array([1]), W_i=np.array([0.7]),
                                 a_e=np.array([310]), a_i=np.array([615]),
                                 b_e=np.array([125]), b_i=np.array([177]),
                                 d_e=np.array([0.16]), d_i=np.array([0.087]),
                                 gamma_e=np.array([0.000641]), gamma_i=np.array([0.001]),
                                 lamda=np.array([0]),
                                 tau_e=np.array([100]), tau_i=np.array([10]),
                                 w_p=np.array([1.4]))

coup = coupling.Linear(a=np.array([1]))
conn.speed=np.array([60])

# Run simulation
tic0=time.time()
sim = simulator.Simulator(model=m, connectivity=conn, coupling=coup,  integrator=integrator, monitors=mon)
sim.configure()

output = sim.run(simulation_length=simLength)
print("Simulation time: %0.2f sec" % (time.time() - tic0,))
# Extract data cutting initial transient
raw_data = output[0][1][transient:, 0, :, 0].T
raw_time = output[0][0][transient:]
regionLabels = conn.region_labels
regionLabels=list(regionLabels)
regionLabels.insert(0,"AVG")

# average signals to obtain mean signal frequency peak
data = np.asarray([np.average(raw_data, axis=0)])
data = np.concatenate((data, raw_data), axis=0)  # concatenate mean signal: data[0]; with raw_data: data[1:end]

# Check initial transient and cut data
timeseriesPlot(data[0:10], raw_time, regionLabels, main_folder, True)
# Fourier Analysis plot
FFTplot(data[0:10], simLength, regionLabels, main_folder, True)

Simulation time: 0.52 sec


## Parameters from Deco (2014) - FFI version
FFI - Feedforward inhibition. It adds long-range connections from excitatory subnodes in one region to inhibitory subnodes of other regions. 

In [4]:
m = models.ReducedWongWangExcInh(G=np.array([2]), I_o=np.array([0.382]),
                                 J_N=np.array([0.15]), J_i=np.array([1]),
                                 W_e=np.array([1]), W_i=np.array([0.8]),
                                 a_e=np.array([310]), a_i=np.array([615]),
                                 b_e=np.array([125]), b_i=np.array([177]),
                                 d_e=np.array([0.16]), d_i=np.array([0.087]),
                                 gamma_e=np.array([0.000641]), gamma_i=np.array([0.001]),
                                 lamda=np.array([1]),
                                 tau_e=np.array([100]), tau_i=np.array([10]),
                                 w_p=np.array([1.4]))

coup = coupling.Linear(a=np.array([1])) # Wong-Wang Inh-Exc includes its own G coupling factor. 
conn.speed=np.array([6])

# Run simulation
tic0=time.time()
sim = simulator.Simulator(model=m, connectivity=conn, coupling=coup,  integrator=integrator, monitors=mon)
sim.configure()

output = sim.run(simulation_length=simLength)
print("Simulation time: %0.2f sec" % (time.time() - tic0,))
# Extract data cutting initial transient
raw_data = output[0][1][transient:, 0, :, 0].T
raw_time = output[0][0][transient:]
regionLabels = conn.region_labels
regionLabels=list(regionLabels)

raw_Si = output[0][1][:, 1, :, 0].T
timeseriesPlot(raw_Si[0:10], raw_time, regionLabels, main_folder, True)

regionLabels.insert(0,"AVG")




# average signals to obtain mean signal frequency peak
data = np.asarray([np.average(raw_data, axis=0)])
data = np.concatenate((data, raw_data), axis=0)  # concatenate mean signal: data[0]; with raw_data: data[1:end]

# Check initial transient and cut data
timeseriesPlot(data[0:10], raw_time, regionLabels, main_folder, True)


# Fourier Analysis plot
FFTplot(data[0:10], simLength, regionLabels, main_folder, True)

Simulation time: 0.74 sec


## Parameters from Zimmermann (2018)

There is some inconsitency when reporting w_p parameter. Take special consideration for tunning.

In [5]:
m = models.ReducedWongWangExcInh(G=np.array([2]), I_o=np.array([0.382]),
                                 J_N=np.array([0.15]), J_i=np.array([1]),
                                 W_e=np.array([1]), W_i=np.array([0.7]),
                                 a_e=np.array([310]), a_i=np.array([615]),
                                 b_e=np.array([125]), b_i=np.array([177]),
                                 d_e=np.array([0.16]), d_i=np.array([0.087]),
                                 gamma_e=np.array([0.000641]), gamma_i=np.array([0.001]),
                                 lamda=np.array([0]),
                                 tau_e=np.array([100]), tau_i=np.array([10]),
                                 w_p=np.array([1.4]))


# Run simulation
tic0=time.time()
sim = simulator.Simulator(model=m, connectivity=conn, coupling=coup,  integrator=integrator, monitors=mon)
sim.configure()

output = sim.run(simulation_length=simLength)
print("Simulation time: %0.2f sec" % (time.time() - tic0,))
# Extract data cutting initial transient
raw_data = output[0][1][transient:, 0, :, 0].T
raw_time = output[0][0][transient:]
regionLabels = conn.region_labels
regionLabels=list(regionLabels)
regionLabels.insert(0,"AVG")

# average signals to obtain mean signal frequency peak
data = np.asarray([np.average(raw_data, axis=0)])
data = np.concatenate((data, raw_data), axis=0)  # concatenate mean signal: data[0]; with raw_data: data[1:end]

# Check initial transient and cut data
timeseriesPlot(data[0:10], raw_time, regionLabels, main_folder, True)
# Fourier Analysis plot
FFTplot(data[0:10], simLength, regionLabels, main_folder, True)

Simulation time: 0.51 sec


## TVB default parameters

In [6]:
m = models.ReducedWongWangExcInh(G=np.array([0.9315]), I_o=np.array([0.382]),
                                 J_N=np.array([0.1716]), J_i=np.array([1.4]),
                                 W_e=np.array([1]), W_i=np.array([0.7]),
                                 a_e=np.array([310]), a_i=np.array([615]),
                                 b_e=np.array([125]), b_i=np.array([177]),
                                 d_e=np.array([0.16]), d_i=np.array([0.087]),
                                 gamma_e=np.array([0.000641]), gamma_i=np.array([0.001]),
                                 lamda=np.array([0]),
                                 tau_e=np.array([100]), tau_i=np.array([10]),
                                 w_p=np.array([1.5219]))


# Run simulation
tic0=time.time()
sim = simulator.Simulator(model=m, connectivity=conn, coupling=coup,  integrator=integrator, monitors=mon)
sim.configure()

output = sim.run(simulation_length=simLength)
print("Simulation time: %0.2f sec" % (time.time() - tic0,))
# Extract data cutting initial transient
raw_data = output[0][1][transient:, 0, :, 0].T
raw_time = output[0][0][transient:]
regionLabels = conn.region_labels
regionLabels=list(regionLabels)
regionLabels.insert(0,"AVG")

# average signals to obtain mean signal frequency peak
data = np.asarray([np.average(raw_data, axis=0)])
data = np.concatenate((data, raw_data), axis=0)  # concatenate mean signal: data[0]; with raw_data: data[1:end]

# Check initial transient and cut data
timeseriesPlot(data[0:10], raw_time, regionLabels, main_folder, True)
# Fourier Analysis plot
FFTplot(data[0:10], simLength, regionLabels, main_folder, True)

Simulation time: 0.54 sec


# Wong-Wang w/ linearized Inhibition
-----
## Parameters from Deco (2013)

In [7]:
m = models.ReducedWongWang(I_o=np.array([0.3]), J_N=np.array([0.2609]),
                           a=np.array([0.27]), b=np.array([0.108]), d=np.array([154]),
                           gamma=np.array([0.641]), sigma_noise=np.array([0.001]),
                           tau_s=np.array([100]), w=np.array([0.9]))

# Coupling function
coup = coupling.Linear(a=np.array([0.8]))

# Run simulation
tic0=time.time()
sim = simulator.Simulator(model=m, connectivity=conn, coupling=coup,  integrator=integrator, monitors=mon)
sim.configure()

output = sim.run(simulation_length=simLength)
print("Simulation time: %0.2f sec" % (time.time() - tic0,))
# Extract data cutting initial transient
raw_data = output[0][1][transient:, 0, :, 0].T
raw_time = output[0][0][transient:]
regionLabels = conn.region_labels
regionLabels=list(regionLabels)
regionLabels.insert(0,"AVG")

# average signals to obtain mean signal frequency peak
data = np.asarray([np.average(raw_data, axis=0)])
data = np.concatenate((data, raw_data), axis=0)  # concatenate mean signal: data[0]; with raw_data: data[1:end]

# Check initial transient and cut data
timeseriesPlot(data[0:10], raw_time, regionLabels, main_folder, True)
# Fourier Analysis plot
FFTplot(data[0:10], simLength, regionLabels, main_folder, True)

Simulation time: 0.37 sec


## TVB default parameters

In [8]:
m = models.ReducedWongWang(I_o=np.array([0.33]), J_N=np.array([0.2609]),
                           a=np.array([0.27]), b=np.array([0.108]), d=np.array([154]),
                           gamma=np.array([0.641]), sigma_noise=np.array([0.000000001]),
                           tau_s=np.array([100]), w=np.array([0.6]))

# Coupling function
coup = coupling.Linear(a=np.array([0.2]))

# Run simulation
tic0=time.time()
sim = simulator.Simulator(model=m, connectivity=conn, coupling=coup,  integrator=integrator, monitors=mon)
sim.configure()

output = sim.run(simulation_length=simLength)
print("Simulation time: %0.2f sec" % (time.time() - tic0,))
# Extract data cutting initial transient
raw_data = output[0][1][transient:, 0, :, 0].T
raw_time = output[0][0][transient:]
regionLabels = conn.region_labels
regionLabels=list(regionLabels)
regionLabels.insert(0,"AVG")

# average signals to obtain mean signal frequency peak
data = np.asarray([np.average(raw_data, axis=0)])
data = np.concatenate((data, raw_data), axis=0)  # concatenate mean signal: data[0]; with raw_data: data[1:end]

# Check initial transient and cut data
timeseriesPlot(data[0:10], raw_time, regionLabels, main_folder, True)
# Fourier Analysis plot
FFTplot(data[0:10], simLength, regionLabels, main_folder, True)

Simulation time: 0.47 sec
